<a href="https://colab.research.google.com/github/shiodeaiko/shiodeaiko/blob/main/lu_bunnkai.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#LU分解で連立方程式を解く

In [1]:
import networkx as nx
import matplotlib.pyplot as plt
import scipy.sparse.linalg as scsplinalg
import numpy as np
from matplotlib.animation import PillowWriter, FuncAnimation

from matplotlib.animation import PillowWriter, FuncAnimation
from matplotlib import animation, rc
from IPython.display import HTML

from scipy import sparse
from scipy.sparse.linalg import spsolve
from scipy.sparse import csr_matrix

from scipy import linalg

In [2]:
#グラフの生成
G0=nx.triangular_lattice_graph(10,10)
nbr_mtx=nx.to_numpy_matrix(G0)
G=nx.from_numpy_matrix(nbr_mtx)
pos=nx.spring_layout(G,iterations=100)

In [3]:
#変数宣言
nt=100
#dt=1とする
nnodes=nx.number_of_nodes(G)
edge_list=list(G.edges)
nbr_mtx=nx.to_numpy_matrix(G)

conductivity=np.zeros((nt,nnodes,nnodes)) #D
length=np.zeros((nnodes,nnodes)) #L
pressure=np.zeros((nt,nnodes)) #p
flux=np.zeros(nnodes) #Q

In [4]:
#初期値と定数の設定
conductivity[0]=nbr_mtx #各エッジの流れやすさは最初1.0
length=nbr_mtx #今回は各エッジの長さは1.0とする
I0=2.0

source_list=[0] #流入口
sink_list=[i+1 for i in range(65)] #残りすべて流出口
source_len=len(source_list)
sink_len=len(sink_list)

for i in source_list:
    flux[i]=I0

#餌ノードの量が全体で保存されるように調整する
for i in sink_list:
    flux[i]=-I0*(source_len/sink_len)

gamma=1.5

In [5]:
#ゼロ除算が発生しないように非ゼロ要素のみで割り算を行う
def divide_non_zero_element(D,L,num_nodes,list_edges):
    X=np.zeros((num_nodes,num_nodes))
    for i,j in list_edges:
        X[i,j]=D[i,j]/L[i,j]
        X[j,i]=D[j,i]/L[j,i]
    return X

#f(Q) for dD/dt 
def f(x):
    powered=x**gamma
    return powered/(powered+1)

#Dの時間変化量を求める
def dD(D,L,p,num_nodes,list_edges):
    X=divide_non_zero_element(D,L,num_nodes,list_edges)
    Q=np.multiply(X,np.expand_dims(p,axis=1)-p)
    ans=f(np.abs(Q))
    return ans

#一次連立方程式を解きpを求める
def deduce_p(D,L,B,num_nodes,list_edges):
    Y=divide_non_zero_element(D,L,num_nodes,list_edges)    
    A=np.diag(np.sum(Y,axis=1))-Y
    lu, p = linalg.lu_factor(A)
    x=linalg.lu_solve((lu, p),B)
    return x

In [6]:
#pの初期値を求める
pressure[0]=deduce_p(conductivity[0],length,flux,nnodes,edge_list)

#繰り返し計算する
for t in range(0,nt-1):
    conductivity[t+1]=dD(conductivity[t],length,pressure[t],nnodes,edge_list)
    pressure[t+1]=deduce_p(conductivity[t+1],length,flux,nnodes,edge_list)

In [7]:
%matplotlib nbagg
fig=plt.figure()

datatype1=[('conductivity',float)]

def animate(i):
    A=np.matrix(conductivity[i],dtype=datatype1)
    G1=nx.from_numpy_matrix(A)
    weights=[G1[u][v]['conductivity'] for u,v in G1.edges()] * 100
  
    
    plt.cla()
    nx.draw_networkx(G,pos,width=weights,node_size=10)
    nx.draw_networkx_nodes(G,pos,node_size=50,
                           node_color=pressure[i],cmap=plt.cm.brg)
    plt.axis('off')
    plt.title('t=' + str(i))
    #plt.show()


# アニメーションの設定
ani = animation.FuncAnimation(fig,animate,frames=nt,repeat=True)


# colabでアニメーションを動かすためのコード
rc('animation', html='jshtml')
ani



<IPython.core.display.Javascript object>